# Make clean data

In [11]:
import pandas as pd

bubbleList = []
countingList = []
mergeList = []
quickList = []
readCSVList = []
pcList = ["6", "16", "21", "23"]

for i in range(len(pcList)):
    bubbleList.append(pd.read_csv("Results"+pcList[i]+"/bubbleSort-PC"+pcList[i]+".csv"))
    bubbleList[i].columns=["Test name","PKG (J)","CPU (J)","GPU (J)","DRAM (J)","Temp (C)","Time (ms)"]

for i in range(len(pcList)):
    countingList.append(pd.read_csv("Results"+pcList[i]+"/countingSort-PC"+pcList[i]+".csv"))
    countingList[i].columns=["Test name","PKG (J)","CPU (J)","GPU (J)","DRAM (J)","Temp (C)","Time (ms)"]
    
for i in range(len(pcList)):
    mergeList.append(pd.read_csv("Results"+pcList[i]+"/mergeSort-PC"+pcList[i]+".csv"))
    mergeList[i].columns=["Test name","PKG (J)","CPU (J)","GPU (J)","DRAM (J)","Temp (C)","Time (ms)"]

for i in range(len(pcList)):
    quickList.append(pd.read_csv("Results"+pcList[i]+"/quickSort-PC"+pcList[i]+".csv"))
    quickList[i].columns=["Test name","PKG (J)","CPU (J)","GPU (J)","DRAM (J)","Temp (C)","Time (ms)"]

for i in range(len(pcList)):
    readCSVList.append(pd.read_csv("Results"+pcList[i]+"/readCSV-PC"+pcList[i]+".csv"))
    readCSVList[i].columns=["Test name","PKG (J)","CPU (J)","GPU (J)","DRAM (J)","Temp (C)","Time (ms)"]



In [12]:
def removeNonsense(df):
    df = df[df["PKG (J)"]>=0]
    df = df[df["CPU (J)"]>=0]
    df = df[df["Time (ms)"]>=0]
    return df

In [13]:
def makeinputColumn(df):
    l = []
    for i in range(len(df)):
        l.append(df.iloc[i]["Test name"].split("-")[0])

    df["Input case"] = l

def makeSizecolumn(df):
    l = []
    for i in range(len(df)):
        l.append(int(df.iloc[i]["Test name"].split("-")[1]))

    df["Size"] = l

In [14]:
def makeinputColumn_readCSV(df):
    l = []
    for i in range(len(df)):
        l.append(df.iloc[i]["Test name"].split("-")[1].lower())
    df["Input case"] = l

def makeSizecolumn_readCSV(df):
    l = []
    for i in range(len(df)):
        l.append(int(df.iloc[i]["Test name"].split("-")[-1]))

    df["Size"] = l

In [15]:
def removeOutliers(df, type_, size, col):
    q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
    q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
    IQR = q3 - q1 
    LF = q1 - 1.5 * IQR
    UF = q3 + 1.5 * IQR

    df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
    df2 = df1[df1["Input case"] == type_][df1["Size"]==size][df1[col] >= LF]
    return df2[col]


In [16]:
def CleanDataframe(df, DataOrBase):
    if DataOrBase == "data":
        cases = ["best", "random", "worst"]
    else:
        cases = ["random", "countingrandom", "countingbest", "countingworst", "mergeworst", "quickbest", "reversesorted", "sorted"]

    cleanList = []
    for case in cases:
        if case != "random" and case != "countingrandom":
            for size in [25000,50000,75000,100000,200000,300000,400000,500000,600000,700000,800000,900000,1000000]:
                cleanPortion = pd.DataFrame({"PKG (J)":[]})
                for col in ["PKG (J)", "CPU (J)", "DRAM (J)","Time (ms)", "Temp (C)"]:
                    cleanPortion[col] = removeOutliers(df, case, size, col)
                
                cleanPortion["Input case"] = [case for _ in range(len(cleanPortion))]
                cleanPortion["Size"] = [int(size) for _ in range(len(cleanPortion))]

                cleanList.append(cleanPortion)
        else:
            for i in range(1,11):
                for size in [25000,50000,75000,100000,200000,300000,400000,500000,600000,700000,800000,900000,1000000]:
                    cleanPortion = pd.DataFrame({"PKG (J)":[]})
                    for col in ["PKG (J)", "CPU (J)", "DRAM (J)","Time (ms)", "Temp (C)"]:
                        cleanPortion[col] = removeOutliers(df, case+str(i), size, col)
                
                    cleanPortion["Input case"] = [case+str(i) for _ in range(len(cleanPortion))]
                    cleanPortion["Size"] = [int(size) for _ in range(len(cleanPortion))]
                    cleanList.append(cleanPortion)
    cleanBubble = pd.concat(cleanList)
    return cleanBubble

In [17]:
def prepareDataframe(df, DataOrBase):
    df = removeNonsense(df)

    if DataOrBase == "data":
        makeinputColumn(df)
        makeSizecolumn(df)
    else:
        makeinputColumn_readCSV(df)
        makeSizecolumn_readCSV(df)    

    return df


In [18]:
def CleanCSV (df, DataOrBase, name, pcNO):
    ready = prepareDataframe(df, DataOrBase)
    clean = CleanDataframe(ready, DataOrBase).dropna().reset_index(drop=True)
    print(clean)
    clean.to_csv("CleanData\\"+name+"Clean-PC"+pcNO+".csv", sep=",", index=False)

In [19]:
for i in range(len(bubbleList)):
    CleanCSV(bubbleList[i], "data","Bubble",pcList[i])

# for i in range(len(bubbleList)):
#     CleanCSV(countingList[i], "data","Counting",pcList[i])

for i in range(len(bubbleList)):
    CleanCSV(mergeList[i], "data","Merge",pcList[i])

for i in range(len(bubbleList)):
    CleanCSV(quickList[i], "data","Quick",pcList[i])

for i in range(len(bubbleList)):
    CleanCSV(readCSVList[i], "base","readCSV",pcList[i])

C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match 

          PKG (J)     CPU (J)   DRAM (J)   Time (ms)  Temp (C) Input case  \
0        3.821045    3.359009   0.187866     418.185      81.0       best   
1        3.808594    3.339966   0.190002     430.416      81.0       best   
2        3.892029    3.450623   0.183533     405.947      81.0       best   
3        3.976379    3.538696   0.187866     392.221      81.0       best   
4        3.803955    3.368225   0.186157     391.750      81.0       best   
...           ...         ...        ...         ...       ...        ...   
10119  778.950439  693.337769  16.698914  107300.000      80.0      worst   
10120  769.609924  684.196533  16.707520  107313.000      80.0      worst   
10121  776.015991  690.558716  16.575073  107332.000      80.0      worst   
10122  776.325867  690.752441  17.068115  107300.000      80.0      worst   
10123  780.807739  694.783081  17.517822  107495.000      80.0      worst   

           Size  
0       25000.0  
1       25000.0  
2       25000.0  
3  

C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match 

          PKG (J)     CPU (J)   DRAM (J)   Time (ms)  Temp (C) Input case  \
0        3.971802    3.439758   0.211914     436.274      67.0       best   
1        3.906067    3.412231   0.196228     387.021      67.0       best   
2        4.092834    3.593201   0.196289     403.466      67.0       best   
3        4.208069    3.704956   0.201599     407.394      67.0       best   
4        3.952576    3.416504   0.207581     446.493      67.0       best   
...           ...         ...        ...         ...       ...        ...   
10224  801.124939  704.917297  18.237854  107265.000      57.0      worst   
10225  815.602600  719.116455  18.233643  107186.000      64.0      worst   
10226  806.500366  709.628906  19.146301  107578.000      57.0      worst   
10227  808.787598  712.215637  18.715515  107361.000      63.0      worst   
10228  804.544067  707.847473  18.875793  107400.000      56.0      worst   

           Size  
0       25000.0  
1       25000.0  
2       25000.0  
3  

C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match 

...

        PKG (J)   CPU (J)  DRAM (J)  Time (ms)  Temp (C) Input case     Size
0      2.240601  1.966187  0.134399    227.880      53.0    random1    25000
1      2.062317  1.775085  0.126160    250.212      53.0    random1    25000
2      2.140869  1.876709  0.121887    222.526      53.0    random1    25000
3      2.217102  1.940735  0.133545    226.620      53.0    random1    25000
4      2.058533  1.796814  0.119385    219.516      53.0    random1    25000
...         ...       ...       ...        ...       ...        ...      ...
36555  7.584045  6.620728  0.382446    805.509      69.0     sorted  1000000
36556  7.647522  6.666382  0.386780    817.192      69.0     sorted  1000000
36557  7.715393  6.740112  0.386230    828.109      70.0     sorted  1000000
36558  7.573486  6.611694  0.383301    816.762      70.0     sorted  1000000
36559  7.495056  6.534302  0.386780    784.613      71.0     sorted  1000000

[36560 rows x 7 columns]


C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match 

        PKG (J)   CPU (J)  DRAM (J)  Time (ms)  Temp (C) Input case     Size
0      2.406616  2.109619  0.141968    224.512      55.0    random1    25000
1      2.154724  1.908997  0.122498    205.914      55.0    random1    25000
2      2.194763  1.939209  0.124695    212.467      55.0    random1    25000
3      2.199951  1.943970  0.129822    218.626      55.0    random1    25000
4      2.398743  2.124756  0.140442    225.795      55.0    random1    25000
...         ...       ...       ...        ...       ...        ...      ...
34926  7.936279  6.956116  0.412476    829.694      63.0     sorted  1000000
34927  7.711365  6.718872  0.404297    771.045      63.0     sorted  1000000
34928  7.615417  6.687134  0.409119    773.986      63.0     sorted  1000000
34929  7.690735  6.708496  0.406128    780.941      63.0     sorted  1000000
34930  7.768188  6.832275  0.409607    799.985      63.0     sorted  1000000

[34931 rows x 7 columns]


C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q3 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.75)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df1 = df[df["Input case"] == type_][df["Size"]==size][df[col] <= UF]
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  q1 = df[df["Input case"] == type_][df["Size"]==size][col].quantile(q=0.25)
C:\Users\langk\AppData\Local\Temp\ipykernel_12568\2727353117.py:3: UserWarning: Boolean Series key will be reindexed to match 

        PKG (J)   CPU (J)  DRAM (J)  Time (ms)  Temp (C) Input case     Size
0      2.080566  1.818848  0.173523    236.114      56.0    random1    25000
1      2.322266  2.055420  0.191833    230.432      56.0    random1    25000
2      2.065308  1.817383  0.169434    219.194      56.0    random1    25000
3      2.067322  1.824097  0.172241    220.192      56.0    random1    25000
4      2.081299  1.833252  0.170715    219.484      56.0    random1    25000
...         ...       ...       ...        ...       ...        ...      ...
34607  7.855164  6.879150  0.567139    840.185      75.0     sorted  1000000
34608  7.712952  6.750793  0.549561    810.143      75.0     sorted  1000000
34609  7.831177  6.861633  0.556274    832.536      75.0     sorted  1000000
34610  7.785706  6.797607  0.558655    824.412      76.0     sorted  1000000
34611  7.850464  6.858093  0.563477    835.048      75.0     sorted  1000000

[34612 rows x 7 columns]


In [20]:
#CleanCSV(bubbleList[0], "data","Bubble",pcList[0])
